In [80]:
import string
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup
from bs4 import UnicodeDammit
import sqlite3
from itertools import chain
from IPython.core.display import HTML
import re

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [81]:
file = BeautifulSoup(open("html_raw.txt", encoding = 'utf8').read(), "lxml")

In [82]:
#retrieve only the "meaningful" tables
table_list = []
for i in range (0, len(file.find_all('table'))):
    string = pd.read_html(str(file.find_all('table')[i]))
    if len(string) > 1:
        table_list.append(string[0])
print("tada!")

tada!


In [83]:
#check to see if all the good stuff is there
len(table_list)

1282

In [84]:
#add missing columns
table_list[393].loc[15] = ['NaN', 'TRADE MARK', 'HÃ¬nh', 'NaN', 'NaN', 'NaN']
table_list[600].loc[15] = ['NaN', 'GOODS / SERVICES', 'NaN', 'NaN', 'NaN', 'NaN']
table_list[601].loc[15] = ['NaN', 'GOODS / SERVICES', 'NaN', 'NaN', 'NaN', 'NaN']
table_list[601].loc[16] = ['NaN', 'CHUKAN CODE', 'NaN', 'NaN', 'NaN', 'NaN']
table_list[602].loc[16] = ['NaN', 'GOODS / SERVICES', 'NaN', 'NaN', 'NaN', 'NaN']
table_list[603].loc[16] = ['NaN', 'GOODS / SERVICES', 'NaN', 'NaN', 'NaN', 'NaN']
table_list[886].loc[16] = ['NaN', 'GOODS / SERVICES', 'NaN', 'NaN', 'NaN', 'NaN']

### Tryna extract all info from the raw file and put them into one xlsx file

In [85]:
#create new dataframe
everything = pd.DataFrame(columns = ['APP. NUMBER', 'APP. DATE', 'TRADE MARK', 'TM TYPE', 'TM COLOR', 'GOODS / SERVICES', 'APPLICANT / RIGHT HOLDER', 'CHUKAN CODE'])

for table in table_list:
    #put to dataframe
    df = table.transpose()
    #replace default column headers as first row
    df.columns = df.iloc[1]
    #delete redundant rows and columns
    df = df.drop(df.index[[0, 1, 3, 4, 5]])
    df = df[['APP. NUMBER', 'APP. DATE', 'TRADE MARK', 'TM TYPE', 'TM COLOR', 'GOODS / SERVICES', 'APPLICANT / RIGHT HOLDER', 'CHUKAN CODE']]
    everything = pd.concat([everything, df], ignore_index=True)

In [86]:
everything.head()

1   APP. NUMBER   APP. DATE TRADE MARK TM TYPE TM COLOR  \
0  4-2015-00658  12/01/2015    Malimbo  Normal        0   
1  4-2015-00659  12/01/2015     Yunyan  Normal        0   
2  4-2015-00660  12/01/2015  GOLD MONT  Normal        0   
3  4-2015-00958  14/01/2015   DIRECTOR  Normal        0   
4  4-2015-01030  14/01/2015      HÃ¬nh  Normal        0   

1                                   GOODS / SERVICES  \
0                            34 Thuá»c lÃ¡ Äiáº¿u.   
1                            34 Thuá»c lÃ¡ Äiáº¿u.   
2                            34 Thuá»c lÃ¡ Äiáº¿u.   
3                            34 Thuá»c lÃ¡ Äiáº¿u.   
4  16 Giáº¥y [vÄn phÃ²ng pháº©m], bÃ¬a cá»©ng [v...   

1                           APPLICANT / RIGHT HOLDER  \
0  CÃ´ng ty trÃ¡ch nhiá»m há»¯u háº¡n HÆ°ng Hiá»...   
1  CÃ´ng ty trÃ¡ch nhiá»m há»¯u háº¡n HÆ°ng Hiá»...   
2  CÃ´ng ty trÃ¡ch nhiá»m há»¯u háº¡n HÆ°ng Hiá»...   
3  CÃ´ng ty trÃ¡ch nhiá»m há»¯u háº¡n má»t thÃ ...   
4  MEDI plus TEC Medizinisch-technische Handelsge...   

1                                        CHUKAN CODE  
0  (10/02/2015) 221: Notification for Acceptance ...  
1  (10/02/2015) 221: Notification for Acceptance ...  
2  (06/02/2015) 221: Notification for Acceptance ...  
3  (28/02/2015) 221: Notification for Acceptance ...  
4  (06/04/2015) 221: Notification for Acceptance ...

In [88]:
#decode the columns so they are readable Vietnamese

for i in range(0, len(everything['GOODS / SERVICES'])):
    everything['GOODS / SERVICES'][i] = str(everything['GOODS / SERVICES'][i]).encode('latin-1').decode('utf8', 'ignore')
    everything['APPLICANT / RIGHT HOLDER'][i] = str(everything['APPLICANT / RIGHT HOLDER'][i]).encode('latin-1').decode('utf8', 'ignore')
    everything['TRADE MARK'][i] = str(everything['TRADE MARK'][i]).encode('latin-1').decode('utf8', 'ignore')

In [89]:
everything.head()

1   APP. NUMBER   APP. DATE TRADE MARK TM TYPE TM COLOR  \
0  4-2015-00658  12/01/2015    Malimbo  Normal        0   
1  4-2015-00659  12/01/2015     Yunyan  Normal        0   
2  4-2015-00660  12/01/2015  GOLD MONT  Normal        0   
3  4-2015-00958  14/01/2015   DIRECTOR  Normal        0   
4  4-2015-01030  14/01/2015       Hình  Normal        0   

1                                   GOODS / SERVICES  \
0                                  34 Thuốc lá điếu.   
1                                  34 Thuốc lá điếu.   
2                                  34 Thuốc lá điếu.   
3                                  34 Thuốc lá điếu.   
4  16 Giấy [văn phòng phẩm], bìa cứng [văn phòng ...   

1                           APPLICANT / RIGHT HOLDER  \
0         Công ty trách nhiệm hữu hạn Hưng Hiệp Phát   
1         Công ty trách nhiệm hữu hạn Hưng Hiệp Phát   
2         Công ty trách nhiệm hữu hạn Hưng Hiệp Phát   
3  Công ty trách nhiệm hữu hạn một thành viên thu...   
4  MEDI plus TEC Medizinisch-technische Handelsge...   

1                                        CHUKAN CODE  
0  (10/02/2015) 221: Notification for Acceptance ...  
1  (10/02/2015) 221: Notification for Acceptance ...  
2  (06/02/2015) 221: Notification for Acceptance ...  
3  (28/02/2015) 221: Notification for Acceptance ...  
4  (06/04/2015) 221: Notification for Acceptance ...

In [25]:
'''
#add image link
everything['Image'] = ''    

counter = 0 
for number in everything['APP. NUMBER']:
    for table in file.find_all('table'):
        #if the app number is present in the table:
        if str(number) in str(table):
            try:
                #append src tag of the image to the current dataframe
                everything['Image'][everything.loc[everything['APP. NUMBER']==number].index[0]] = table.find_all('img')[0]['src']
            except:
                everything['Image'][everything.loc[everything['APP. NUMBER']==number].index[0]] = 'NaN'
            print (counter)
            counter += 1
print('Eyy made it!')
#export to excel file
#everything.to_excel("Everything.xlsx")
'''

'\n#add image link\neverything[\'Image\'] = \'\'    \n\ncounter = 0 \nfor number in everything[\'APP. NUMBER\']:\n    for table in file.find_all(\'table\'):\n        #if the app number is present in the table:\n        if str(number) in str(table):\n            try:\n                #append src tag of the image to the current dataframe\n                everything[\'Image\'][everything.loc[everything[\'APP. NUMBER\']==number].index[0]] = table.find_all(\'img\')[0][\'src\']\n            except:\n                everything[\'Image\'][everything.loc[everything[\'APP. NUMBER\']==number].index[0]] = \'NaN\'\n            print (counter)\n            counter += 1\nprint(\'Eyy made it!\')\n#export to excel file\n#everything.to_excel("Everything.xlsx")\n'

-------------------------------------------------------------------------------------------------------------------------------

### British American Tobacco

In [8]:
#retrieve lists that contain "British American Tobacco"
bat = []
for table in table_list:
    if any('British American' in s for s in list(table[2].astype(str))):
        bat.append(table)
print('Tada!')

Tada!


In [9]:
len(bat)

60

In [12]:
bat_clean = pd.DataFrame(columns = ['APP. NUMBER', 'APP. DATE', 'TRADE MARK', 'TM TYPE', 'TM COLOR', 'GOODS / SERVICES', 'APPLICANT / RIGHT HOLDER', 'CHUKAN CODE'])
for table in bat:
    #put to dataframe
    df = table.transpose()
    #replace default column headers as first row
    df.columns = df.iloc[1]
    #delete redundant rows and columns
    df = df.drop(df.index[[0, 1, 3, 4, 5]])
    df = df[['APP. NUMBER', 'APP. DATE', 'TRADE MARK', 'TM TYPE', 'TM COLOR', 'GOODS / SERVICES', 'APPLICANT / RIGHT HOLDER', 'CHUKAN CODE']]
    bat_clean = pd.concat([bat_clean, df], ignore_index=True)
bat_clean


NameError: name 'bat' is not defined

In [20]:
#export to excel file
bat_clean.to_excel("British American Tobacco.xlsx")

### Philip Morris

In [11]:
#retrieve lists that contain "Philip Morris"
pmi = []
for table in table_list:
    if any('Philip Morris' in s for s in list(table[2].astype(str))):
        pmi.append(table)
print('Tada!')

Tada!


In [12]:
len(pmi)

87

In [18]:
#fix frames that have no trade mark column
pmi[50].loc[15] = ['NaN', 'TRADE MARK', 'HÃ¬nh', 'NaN', 'NaN', 'NaN']
pmi[50]

0  \
0                                               INID   
1                                               INID   
2                                              FIELD   
3                                            CONTENT   
4                                              (210)   
5                                              (220)   
6                                              (300)   
7                                                NaN   
8                                                NaN   
9                                              (511)   
10                                     (731) / (732)   
11                                               NaN   
12  Quai Jeanrenaud 3, NeuchÃ¢tel, 2000, Switzerland   
13                                             (740)   
14                                               NaN   
15                                               NaN   

                           1  \
0                       INID   
1                        NaN   
2                        NaN   
3                        NaN   
4                APP. NUMBER   
5                  APP. DATE   
6              PRIORITY DATE   
7                    TM TYPE   
8                   TM COLOR   
9           GOODS / SERVICES   
10  APPLICANT / RIGHT HOLDER   
11         APPLICANT ADDRESS   
12                       NaN   
13                 IP AGENCY   
14               CHUKAN CODE   
15                TRADE MARK   

                                                    2  \
0                                               FIELD   
1                                                 NaN   
2                                                 NaN   
3                                                 NaN   
4                                        4-2016-30951   
5                                          05/10/2016   
6                                                 NaN   
7                                              Normal   
8                                                   0   
9   34 Thuá»c lÃ¡, thÃ´ hoáº·c ÄÃ£ ÄÆ°á»£c cháº...   
10                        Philip Morris Products S.A.   
11   Quai Jeanrenaud 3, NeuchÃ¢tel, 2000, Switzerland   
12                                                NaN   
13                                               TGVN   
14  (04/11/2016) 221: Notification for Acceptance ...   
15                                              HÃ¬nh   

                                                   3        4        5  
0                                              FIELD  CONTENT  CONTENT  
1                                                NaN      NaN      NaN  
2                                                NaN      NaN      NaN  
3                                                NaN      NaN      NaN  
4                                                NaN      NaN      NaN  
5                                                NaN      NaN      NaN  
6                                                NaN      NaN      NaN  
7                                                NaN      NaN      NaN  
8                                                NaN      NaN      NaN  
9                                                NaN      NaN      NaN  
10                                               NaN      NaN      NaN  
11  Quai Jeanrenaud 3, NeuchÃ¢tel, 2000, Switzerland      NaN      NaN  
12                                               NaN      NaN      NaN  
13                                               NaN      NaN      NaN  
14                                               NaN      NaN      NaN  
15                                               NaN      NaN      NaN

In [19]:
pmi_clean = pd.DataFrame(columns = ['APP. NUMBER', 'APP. DATE', 'TRADE MARK', 'TM TYPE', 'TM COLOR', 'GOODS / SERVICES', 'APPLICANT / RIGHT HOLDER', 'CHUKAN CODE'])
for table in pmi:
    #put to dataframe
    df = table.transpose()
    #replace default column headers as first row
    df.columns = df.iloc[1]
    #delete redundant rows and columns
    df = df.drop(df.index[[0, 1, 3, 4, 5]])
    df = df[['APP. NUMBER', 'APP. DATE', 'TRADE MARK', 'TM TYPE', 'TM COLOR', 'GOODS / SERVICES', 'APPLICANT / RIGHT HOLDER', 'CHUKAN CODE']]
    pmi_clean = pd.concat([pmi_clean, df], ignore_index=True)
    print('haha')
pmi_clean

haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha
haha


1    APP. NUMBER   APP. DATE  \
0   4-2015-26281  24/09/2015   
1   4-2015-26582  28/09/2015   
2   4-2015-34716  09/12/2015   
3   4-2015-34717  09/12/2015   
4   4-2015-34718  09/12/2015   
5   4-2016-01030  13/01/2016   
6   4-2016-01031  13/01/2016   
7   4-2016-04509  26/02/2016   
8   4-2016-04510  26/02/2016   
9   4-2016-04511  26/02/2016   
10  4-2016-04512  26/02/2016   
11  4-2016-04513  26/02/2016   
12  4-2016-04514  26/02/2016   
13  4-2016-04515  26/02/2016   
14  4-2016-04516  26/02/2016   
15  4-2016-04517  26/02/2016   
16  4-2016-04518  26/02/2016   
17  4-2016-04519  26/02/2016   
18  4-2016-04520  26/02/2016   
19  4-2016-04521  26/02/2016   
20  4-2016-04522  26/02/2016   
21  4-2016-04523  26/02/2016   
22  4-2016-04524  26/02/2016   
23  4-2016-04525  26/02/2016   
24  4-2016-04526  26/02/2016   
25  4-2016-04527  26/02/2016   
26  4-2016-04528  26/02/2016   
27  4-2016-04529  26/02/2016   
28  4-2016-04530  26/02/2016   
29  4-2016-04531  26/02/2016   
30  4-2016-04532  26/02/2016   
31  4-2016-04533  26/02/2016   
32  4-2016-04534  26/02/2016   
33  4-2016-04535  26/02/2016   
34  4-2016-04536  26/02/2016   
35  4-2016-04537  26/02/2016   
36  4-2016-04538  26/02/2016   
37  4-2016-04539  26/02/2016   
38  4-2016-04540  26/02/2016   
39  4-2016-04541  26/02/2016   
40  4-2016-04544  26/02/2016   
41  4-2016-04938  02/03/2016   
42  4-2016-16153  02/06/2016   
43  4-2016-16154  02/06/2016   
44  4-2016-18076  17/06/2016   
45  4-2016-25254  17/08/2016   
46  4-2016-28452  14/09/2016   
47  4-2016-28453  14/09/2016   
48  4-2016-28454  14/09/2016   
49  4-2016-28983  19/09/2016   
50  4-2016-30951  05/10/2016   
51  4-2016-30952  05/10/2016   
52  4-2016-33588  26/10/2016   
53  4-2016-35827  11/11/2016   
54  4-2016-35828  11/11/2016   
55  4-2016-36243  15/11/2016   
56  4-2016-36244  15/11/2016   
57  4-2017-00336  06/01/2017   
58  4-2017-02741  14/02/2017   
59  4-2017-03236  20/02/2017   
60  4-2017-15095  26/05/2017   
61  4-2017-15096  26/05/2017   
62  4-2017-15097  26/05/2017   
63  4-2017-15098  26/05/2017   
64  4-2017-28844  11/09/2017   
65  4-2017-30040  19/09/2017   
66  4-2017-32132  04/10/2017   
67  4-2017-33128  11/10/2017   
68  4-2017-33666  16/10/2017   
69  4-2017-37146  10/11/2017   
70  4-2017-37147  10/11/2017   
71  4-2017-39666  29/11/2017   
72  4-2017-41064  08/12/2017   
73  4-2017-41065  08/12/2017   
74  4-2018-02875  24/01/2018   
75  4-2018-03194  26/01/2018   
76  4-2018-15402  16/05/2018   
77  4-2018-15403  16/05/2018   
78  4-2018-15404  16/05/2018   
79  4-2018-17614  31/05/2018   
80  4-2018-17615  31/05/2018   
81  4-2018-22346  06/07/2018   
82  4-2018-25546  31/07/2018   
83  4-2018-25547  31/07/2018   
84  4-2018-34028  02/10/2018   
85  4-2018-34029  02/10/2018   
86  4-2019-01115  09/01/2019   

1                                          TRADE MARK TM TYPE TM COLOR  \
0                                          AQUA SPRAY  Normal        0   
1                                     PACK LOK, hÃ¬nh  Normal        1   
2                                            CLEANTIP  Normal        0   
3                                  clear taste, hÃ¬nh  Normal        0   
4                                     RECESSED, hÃ¬nh  Normal        0   
5                                               HÃ¬nh  Normal        0   
6                                 Chesterfield, hÃ¬nh  Normal        0   
7                                               HÃ¬nh  Normal        0   
8                                              BEYOND  Normal        0   
9                                     Marlboro, hÃ¬nh  Normal        0   
10                            DON'T BE A MAYBE, hÃ¬nh  Normal        0   
11                               NO MORE MAYBE, hÃ¬nh  Normal        0   
12                                       MAYBE, hÃ¬nh  Normal        1   
13                                             ALPINE  Normal        0   
14                                        BOND STREET  Normal        0   

In [22]:
#export to excel file
pmi_clean.to_excel("Philip Morris.xlsx")

### Japan Tobacco Inc

In [24]:
#retrieve lists that contain "Japan Tobacco Inc"
jti = []
for table in table_list:
    if any('Japan Tobacco' in s for s in list(table[2].astype(str))):
        jti.append(table)
print('Tada!')

Tada!


In [25]:
len(jti)

10

In [26]:
jti[0].transpose()

0     1      2        3             4           5              6   \
0     INID  INID  FIELD  CONTENT         (210)       (220)          (300)   
1     INID   NaN    NaN      NaN   APP. NUMBER   APP. DATE  PRIORITY DATE   
2    FIELD   NaN    NaN      NaN  4-2015-17485  03/07/2015            NaN   
3    FIELD   NaN    NaN      NaN           NaN         NaN            NaN   
4  CONTENT   NaN    NaN      NaN           NaN         NaN            NaN   
5  CONTENT   NaN    NaN      NaN           NaN         NaN            NaN   

                                               7        8         9   \
0                                           (540)      NaN       NaN   
1                                      TRADE MARK  TM TYPE  TM COLOR   
2  MEVIUS FULLSTREAM STREAM FILTER C C [S], hÃ¬nh   Normal         1   
3                                             NaN      NaN       NaN   
4                                             NaN      NaN       NaN   
5                                             NaN      NaN       NaN   

                                                  10  \
0                                              (511)   
1                                   GOODS / SERVICES   
2  34 LÃ¡ thuá»c lÃ¡, ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n...   
3                                                NaN   
4                                                NaN   
5                                                NaN   

                                    11  \
0                                (531)   
1                         VIENNA CLASS   
2  01.15.23 11.01.11 26.11.12 26.15.15   
3                                  NaN   
4                                  NaN   
5                                  NaN   

                                                  12  \
0                                              (851)   
1                                         LIMITATION   
2  NhÃ£n hiá»u ÄÆ°á»£c báº£o há» tá»ng thá»....   
3                                                NaN   
4                                                NaN   
5                                                NaN   

                                        13  \
0                            (731) / (732)   
1                 APPLICANT / RIGHT HOLDER   
2  Japan Tobacco Inc. / Japan Tobacco Inc.   
3                                      NaN   
4                                      NaN   
5                                      NaN   

                                         14  \
0                                       NaN   
1                         APPLICANT ADDRESS   
2  2-2-1 Toranomon, Minato-ku, Tokyo, Japan   
3  2-2-1 Toranomon, Minato-ku, Tokyo, Japan   
4                                       NaN   
5                                       NaN   

                                         15  \
0  2-2-1 Toranomon, Minato-ku, Tokyo, Japan   
1                                       NaN   
2                                       NaN   
3                                       NaN   
4                                       NaN   
5                                       NaN   

                                         16  \
0                                       NaN   
1                      RIGHT HOLDER ADDRESS   
2  2-2-1 Toranomon, Minato-ku, Tokyo, Japan   
3  2-2-1 Toranomon, Minato-ku, Tokyo, Japan   
4                                       NaN   
5                                       NaN   

                                         17             18          19  \
0  2-2-1 Toranomon, Minato-ku, Tokyo, Japan          (111)         NaN   
1                                       NaN    REG. NUMBER   REG. DATE   
2                                       NaN  4-0287168-000  29/08/2017   
3                                       NaN            NaN         NaN   
4                                       NaN            NaN         NaN   
5                                       NaN            NaN         NaN   

                 20           21             22  \

In [27]:
jti_clean = pd.DataFrame(columns = ['APP. NUMBER', 'APP. DATE', 'TRADE MARK', 'TM TYPE', 'TM COLOR', 'GOODS / SERVICES', 'APPLICANT / RIGHT HOLDER', 'CHUKAN CODE'])
for table in jti:
    #put to dataframe
    df = table.transpose()
    #replace default column headers as first row
    df.columns = df.iloc[1]
    #delete redundant rows and columns
    df = df.drop(df.index[[0, 1, 3, 4, 5]])
    df = df[['APP. NUMBER', 'APP. DATE', 'TRADE MARK', 'TM TYPE', 'TM COLOR', 'GOODS / SERVICES', 'APPLICANT / RIGHT HOLDER', 'CHUKAN CODE']]
    jti_clean = pd.concat([jti_clean, df], ignore_index=True)
jti_clean

1   APP. NUMBER   APP. DATE  \
0  4-2015-17485  03/07/2015   
1  4-2015-24573  08/09/2015   
2  4-2015-32071  16/11/2015   
3  4-2016-03613  15/02/2016   
4  4-2016-33622  26/10/2016   
5  4-2017-09591  13/04/2017   
6  4-2017-19641  29/06/2017   
7  4-2018-39531  12/11/2018   
8  4-2018-41862  28/11/2018   
9  4-2018-43530  10/12/2018   

1                                         TRADE MARK TM TYPE TM COLOR  \
0     MEVIUS FULLSTREAM STREAM FILTER C C [S], hÃ¬nh  Normal        1   
1                                              HÃ¬nh  Normal        0   
2  MEVIUS LESS SMOKE SMELL LSS AIRSTREAM STREAM F...  Normal        1   
3                                             CASTER  Normal        0   
4                                               NOVA  Normal        0   
5                                     WINSTON PURPLE  Normal        0   
6                                           ACTIVATE  Normal        0   
7                               MEVIUS OPTION, hÃ¬nh  Normal        1   
8                                          SYMPHONIC  Normal        0   
9                                          BLACK TEA  Normal        0   

1                                   GOODS / SERVICES  \
0  34 LÃ¡ thuá»c lÃ¡, ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n...   
1  34 Thuá»c lÃ¡ ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n hoáº...   
2  34 LÃ¡ thuá»c lÃ¡, ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n...   
3  34 Thuá»c lÃ¡ ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n hoáº...   
4  34 LÃ¡ thuá»c lÃ¡, ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n...   
5  34 Thuá»c lÃ¡ ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n hoáº...   
6  34 Thuá»c lÃ¡ ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n hoáº...   
7  34 LÃ¡ thuá»c lÃ¡, ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n...   
8  34 LÃ¡ thuá»c lÃ¡, ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n...   
9  34 LÃ¡ thuá»c lÃ¡, ÄÃ£ ÄÆ°á»£c cháº¿ biáº¿n...   

1                 APPLICANT / RIGHT HOLDER  \
0  Japan Tobacco Inc. / Japan Tobacco Inc.   
1  Japan Tobacco Inc. / Japan Tobacco Inc.   
2                       Japan Tobacco Inc.   
3  Japan Tobacco Inc. / Japan Tobacco Inc.   
4  Japan Tobacco Inc. / Japan Tobacco Inc.   
5                       Japan Tobacco Inc.   
6                       Japan Tobacco Inc.   
7                       Japan Tobacco Inc.   
8                       Japan Tobacco Inc.   
9                       Japan Tobacco Inc.   

1                                        CHUKAN CODE  
0  (31/07/2015) 221: Notification for Acceptance ...  
1  (07/10/2015) 221: Notification for Acceptance ...  
2  (16/12/2015) 221: Notification for Acceptance ...  
3  (15/03/2016) 221: Notification for Acceptance ...  
4  (28/11/2016) 221: Notification for Acceptance ...  
5  (12/05/2017) 221: Notification for Acceptance ...  
6  (31/07/2017) 221: Notification for Acceptance ...  
7  (12/12/2018) 221: Notification for Acceptance ...  
8  (27/12/2018) 221: Notification for Acceptance ...  
9  (10/01/2019) 221: Notification for Acceptance ...

In [ ]:
jti_clean['Image'] = ''
for number in jti_clean['APP. NUMBER']:
    for table in file.find_all('table'):
        #if the app number is present in the table:
        if number in str(table):
            #append src tag of the image to the current dataframe
            jti_clean['Image'][jti_clean.loc[jti_clean['APP. NUMBER']==number].index[0]] = table.find_all('img')[0]['src']

In [28]:
#export to excel file
jti_clean.to_excel("Japan Tobacco Inc.xlsx")

In [34]:
a = file.encode('latin-1')

b'<html><body><table border="0" cellpadding="1" width="100%">\n<tr>\n<td height="32" width="6%"><table bgcolor="22ADE7" border="0" cellpadding="0" cellspacing="1" height="32" width="100%">\n<tr><td align="center" background="../Images/box_bgr.gif" bgcolor="#FFFFFF" class="text">INID</td></tr></table>\n</td>\n<td height="32" width="24%"><table bgcolor="22ADE7" border="0" cellpadding="0" cellspacing="1" height="32" width="100%">\n<tr><td align="center" background="../Images/box_bgr.gif" bgcolor="#FFFFFF" class="text">FIELD</td></tr></table>\n</td>\n<td height="70%"><table bgcolor="22ADE7" border="0" cellpadding="0" cellspacing="1" height="32" width="100%">\n<tr><td align="center" background="../Images/box_bgr.gif" bgcolor="#FFFFFF" class="text">CONTENT</td></tr></table>\n</td>\n</tr>\n<tr>\n<td align="center" class="jcGridCell" width="6%">(210)</td>\n<td class="jcGridCell" width="24%">APP. NUMBER </td>\n<td class="jcGridCell" width="70%">4-2015-00658</td>\n</tr>\n<tr>\n<td align="center"